______________________________________________________________
# EPS 109 Final Project: Mechanisms of Magnetic Remanence Acquisition 
Leyla Namazie
____________________________________


In [130]:
import numpy as np
import matplotlib.pyplot as plt
from skimage import measure

from matplotlib.animation import FFMpegWriter
metadata = dict(title='My first animation in 3D', artist='Matplotlib',comment='Wakanda is here now.')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)

There are various types of magnetization that can be acquired in rocks. The signals carried by these magnetizations provide important magnetic field directional and positional data that form the basis of the field of paleomagnetism. In this assignment, I will make simulations of two common forms of this "magnetic remanence" and how they are acquired when a rock forms. 

    --- Outline ----
    
    SIMULATION ONE: 1D Time Dependent Heat Equation and Thermal Remanence Acquisition 
    SIMULATION TWO: 2D Time Independent Heat Equation and Thermal Remanence Acquisition 
    SIMULATION THREE: Diffusion Limited Aggregation + Image Analysis and Chemical Remanence Acquisition 
    
    -----------------

# Part 1: Crystallization from Magma & Thermal Remanent Magnetism in a Cooling Dike

When magma cools, the microscopic magnetic moments of growing crystals acquire a thermal magnetic remanence that is dependent on the ambient temperature, magnetic field, and the mineral's own crystallographic properties. This first simulation will use the heat equation to model how a basaltic intrusion (with 5% volume of magnetite in a diamagnetic ground mass) cools and acquires a magnetic signal. 

In [131]:
# Define Physical variables
K=0.028 # J/cm/sec/K
c=1.02 # J/g/K
p=2.85 # g/cm^3
k= K/(c*p) # thermal diffusivity

In [132]:
# This function sets up the 1D Heat Equation and is used to reset the temperature distribution in the array space. 
N=50
b1=2
b2=3
T_in = 1150
L=3000

def set_initialsT():
    global T, steps, dx, dt, n, x, steps
    x=np.linspace(0,L,(5*N))
    T=np.zeros(5*N)
    T[int(b1*N):int(b2*N)]=T_in
    dt = 60*60 # units: seconds
    dx = (L/(5*N))
    n= k*dt/(dx**2)
    steps = 5*N

set_initialsT()

Definitions: 
* Single Domain Magnetite: Typically, the strongest and most reliable magnetic signals are held by smaller crystals. These are referred to as "single somain" magnetizations and generally correspond to a mineral diameter of < 1micron. Single domain magnetite is a particularly stable magnetic carrier and will be the focus of this thermal simulation.

* Curie Temperature: the temperature above which a ferromagnetic material loses its magnetic signal. Thermal energy in the crystal lattice overrides the magnetostatic energy that holds magnetic moments in line with the magnetic field 
* Blocking Temperature: the temperature below which a ferromagnetic material acquires "remanence" and the magnetizations is, essentially, locked in place. 
* Magnetic Saturation: The maximum magnitude that a given mineral can be magnetized given some coercive field. 

In [133]:
# This function sets up of the magnetization space of the dike intrusion 
def set_initialsM():
    global M
    M=  np.zeros(5*N)
set_initialsM()

# Single Domain Magnetite Parameters 
Ms_0 = 480*10**3 # magnetic saturation of magnetite (A/m)
Tc = 853 # Curie Temperature (K)
Tb = 823 # Blocking Temperature (K)
T0 = 20 # Surface Temperature (K)

# Magnetic constants 
vol = 4.3*10**-17 *10**-6 # volume of our magnetite mineral sample (m^3)
H = 0.5*10**-4 # surface magnetic field (Teslas)

Magnetic saturation of a mineral is dependent on temperature and is a function of the material's curie temperature: 


[1]

#### $ \frac {M_s(T)}{M_s(T_0)} = (\frac{T_c - T}{T_c - T_0})^\gamma $  


Where T_0 is ambient temperature (20K) and gamma is a constant 

In [134]:
def Ms_at_temp(T):
    gamma = 0.38 
    T0 = 0 # kelvin
    Ms_T = ((Tc-T)/(Tc-T0))**gamma
    return Ms_0*Ms_T
# returns A/m

### SIMULATION 1: Magnetization Acquired in Dike With 1D Heat Equation 

In [135]:
# 6 Months  
set_initialsT()
set_initialsM()
for i in range(24*30*6):
    Tnew=np.copy(T)
    Mnew=np.copy(M)
    for j in range(1,steps -1):
        Tnew[j]=n*(T[j+1]+T[j-1] -2*T[j])+T[j]
        if j>b1*N and j <b2*N: 
            if Tnew[j]>0 and Tnew[j]<(Tb-273):
                Mnew[j] = Ms_at_temp(Tnew[j]+273)
    T=np.copy(Tnew)
    M=np.copy(Mnew)
plt.plot(M, label= "6 months")
print("After 6 Months, the temperature in the middle of the dike is",T[len(T)//2],"°C")


# 1 Year  
set_initialsT()
set_initialsM()
for i in range(24*365):
    Tnew=np.copy(T)
    Mnew=np.copy(M)
    for j in range(1,steps -1):
        Tnew[j]=n*(T[j+1]+T[j-1] -2*T[j])+T[j]
        if j>b1*N and j <b2*N: 
            if Tnew[j]>0 and Tnew[j]<(Tb-273):
                Mnew[j] = Ms_at_temp(Tnew[j]+273)
    T=np.copy(Tnew)
    M=np.copy(Mnew)
plt.plot(M, label = "1 Year")
print("After 1 Year, the temperature in the middle of the dike is",T[len(T)//2],"°C")


# 5 Years 
set_initialsT()
set_initialsM()
for i in range(24*365*5):
    Tnew=np.copy(T)
    Mnew=np.copy(M)
    for j in range(1,steps -1):
        Tnew[j]=n*(T[j+1]+T[j-1] -2*T[j])+T[j]
        if j>b1*N and j <b2*N: 
            if Tnew[j]>0 and Tnew[j]<(Tb-273):
                Mnew[j] = Ms_at_temp(Tnew[j]+273)
    T=np.copy(Tnew)
    M=np.copy(Mnew)
plt.plot(M, label = '5 Years')
print("After 5 Years, the temperature in the middle of the dike is",T[len(T)//2],"°C")

plt.legend()
plt.ylabel("Magnetization (A/m)")
plt.show()

After 6 Months, the temperature in the middle of the dike is 478.8013390253756 °C
After 1 Year, the temperature in the middle of the dike is 344.01069656580324 °C
After 5 Years, the temperature in the middle of the dike is 84.74634623707668 °C


    From this simulation, we can see that the higher the temperature is in the dike, the less intense the magnetization is in that region. This is product of the inverse relationship between thermal and magnetic energy inside ferromagnetic minerals.

### SIMULATION 2: Visualizing Magnetic Acquisition with the 2D Heat Equation 

This simulation will be the same as above, except now using the 2D heat equation. Some spatial variables were altered to speed up processing time. 

In [137]:
%matplotlib osx

# Set up Variables  
N2 = 50
L=30
T=np.zeros([N2,N2])
M=np.zeros([N2,N2])
T_in=1150
T[5:-5,20:30]=T_in

# Set up Plot 
from mpl_toolkits.mplot3d import Axes3D
from matplotlib import cm
X = np.linspace(0, L, N2) # where n is number of segments
Y = np.linspace(0, L, N2)
X, Y = np.meshgrid(X, Y)
fig = plt.figure(dpi=200)

# find the stationary state in 2D 
with writer.saving(fig, "___TRM_2dHeat.mp4", dpi=200):
    for k in range(0,100):
        Tnew= np.copy(T)
        Mnew=np.copy(M)
        for i in range(1,N2-1):
            for j in range(1,N2-1):
                Tnew[i,j]=(T[i+1,j]+T[i-1,j]+T[i,j+1]+T[i,j-1])*.25
                if j>20 and j<30: 
                    if Tnew[i,j]>0 and Tnew[i,j]<(Tb-273):
                        Mnew[i,j] = Ms_at_temp(Tnew[i,j]+273)
        T=np.copy(Tnew)
        M=np.copy(Mnew)
        fig.clear()
        ax = fig.gca(projection='3d')
        ax.plot_surface(X, Y, M, cmap=cm.inferno, antialiased=False)
        plt.draw()
        plt.pause(0.01) # choose the time argument between 0.01 and 0.5
#         writer.grab_frame()

In [ ]:
plt.imshow(M,cmap="inferno")

In [126]:
np.shape(M)

(50, 50)

In [144]:
# fig = plt.figure(dpi=200)
# ax = fig.gca(projection='3d')
# ax.plot_surface(X, Y, M, cmap=cm.inferno, antialiased=False)

    From this simulation, you can more easily visualize the relationship between temperature and rate of magnetization acquisition in the dike. The regions with more heat loss (the edges of the dike) are the first to cool past the "blocking temperature" where in which the crystal has developed enough structure (referred to as crystallographic anisotropy energy) to permanently acquire a magnetization.

# Part 2: Chemical Remanent Magnetization in Growing Hematite Crystals

Another mechanism of magnetism acquisition in rocks is through chemical processes. Chemical Remanent Magnetization (CRM) describes the process where chemically aggregating minerals become magnetization BELOW the curie temperature. Rather than cooling through a blocking temperature that locks in the signal, particles with a CRM must grow past a certain "blocking volume" that will allow them to lock in a magnetic signal. 

* This third simulation will model use diffusion limited aggregation and image analysis techniques to show the relationship between volume and magnetization of hematite particules chemically forming in some diamagnetic matrix.

* The blocking volume of a mineral is defined by the following: 

[2]
#### $ v_b = \frac {k_b T \ln(C \tau)}{K_u} $       


* where C is a frequency constant and tau is the mineral's relaxation time (an indicator of magnetization decay rate) in seconds. Ku is the minerals anisotropy, which is a function of crystallographic properties: Ms (saturation magnetization) and Hc (maximum coercive field). 

[3] 
#### $ K_u = \frac {\mu_0  M_s  H_c}{2} $


First we define an function to model blocking volume equation [2]. This will be used to create an underlying plot that shows how blocking volume relates to a minerals relaxation time (and, thus, magnetism acquisition). 

In [8]:
def blocking_vol(tau,Ku):
    k_bolt = 1.38064852 * 10**-23 # Boltzmann's constant (J/K)
    T=280 # absolute temperature (K)
    C=10**10 # frequency factor (s-1)
    v=(2*k_bolt*T*np.log(C*tau))/Ku # m3
    return v * 10 **18 # returns volume in micrometeres cubed 

# relaxation times to be plotted 
s = 100 # 100 seconds 
Myr = 3.155e13 # 1 million years in seconds 
Gyr = 1.419e17 # 1 billion years in seconds

hematite properties needed for crystallographic anisotropy equation [3]: 

In [9]:
# parameters of equation [3]
mu0_Hc=1.0 # Coervcitiy of hematite (Bc = mu_oH_c in tesla)
Ms_hem= 0.4*5271 # saturation magnetization of hematite (A/m)
Ku_hem = (1/2)*mu0_Hc*Ms_hem *10**-3 # anisotropy constant (kJ/m3)
Ku_hem

1.0542

In [10]:
# values similar to Ku_hem = 1.054 will be used 
# for the unique hematite crystals growing in this simulation 
# these will form the x values of our first plot 

Ku_hemVals = [0.9,1.0,1.05,1.2,1.3]

### SIMULATION THREE: Crystallization of Hematite Below Curie Temperature 

In [92]:
def display(A):
    maxX = A.shape[0]
    maxY = A.shape[1]
    B = np.zeros((maxY, maxX))
    for ix in range(0,maxX):
        for iy in range(0,maxY):
            B[maxY-1-iy,ix] = A[ix,iy]
    plt.rcParams['figure.figsize'] = [6, 6/maxX*maxY]
    axs[1].imshow(B,cmap='GnBu')

In [93]:
# used for color coding charts below
def color_point(code,i):
    if i == 0:
        axs[0].scatter(Ku_hemVals[0],volumes[0],marker='o',color='dimgray',edgecolors=code)
    if i == 1:
        axs[0].scatter(Ku_hemVals[1],volumes[1],marker='o',color='darkgray',edgecolors=code)
    if i == 2:
        axs[0].scatter(Ku_hemVals[2],volumes[2],marker='o',color='lightgray',edgecolors=code)
    if i == 3:
        axs[0].scatter(Ku_hemVals[3],volumes[3],marker='o',color='whitesmoke',edgecolors=code)
    if i == 4:
        axs[0].scatter(Ku_hemVals[4],volumes[4],marker='o',color='white',edgecolors=code)            

In [107]:
Ku = np.linspace(0.1,5000,500000)

def display_volumes(A):
    global volumes, labels
    axs[0].clear()
    
    # plot various relaxation times 
    axs[0].plot(Ku,blocking_vol(s,Ku),color='b',label='tau = 100 s')
    axs[0].plot(Ku,blocking_vol(Myr,Ku),color='g',label='tau = 1 Myr')
    axs[0].plot(Ku,blocking_vol(Gyr,Ku),color='r',label='tau = 4.5 Gyr')                
    
    axs[0].set_ylim([0, 1])
    axs[0].set_xlim([0, 5])
    axs[0].set_xlabel("anisotropy energy density (microns kJ/m^3)")
    axs[0].set_ylabel("grain volume (µm^3)")

    # label each growing crystal and assign areas and volumes   
    labels = measure.label(A)
    props = measure.regionprops(labels)
    grain_areas = []
    volumes = []
    for p in props:
        grain_areas.append(p.area)
    for item in grain_areas: 
        volumes.append (item * 1 * 10**-3)
    
    # plot volumes 
    for i in range(len(volumes)):
        if volumes[i] < blocking_vol(s,Ku_hemVals[i]):
            color_point('black',i)

        if volumes[i] > blocking_vol(s,Ku_hemVals[i]) and volumes[i] < blocking_vol(Myr,Ku_hemVals[i]):
            color_point('blue',i)

        if volumes[i] > blocking_vol(Myr,Ku_hemVals[i]) and volumes[i] < blocking_vol(Gyr,Ku_hemVals[i]):
            color_point('green',i)
            
        if volumes[i] > blocking_vol(Gyr,Ku_hemVals[i]):
            color_point('red',i)
    
    plt.imshow(labels,cmap='gray')

    
  

In [108]:
# create matrix space where each xy index represents a nanometer 

nParticles = 100000
maxX = 110
maxY = 110

A = np.zeros((maxX, maxY))
A[15,25] = 1 # label: 1; top left grain; dimgray
A[25,80] = 1 # label: 2; top right grain; darkgray
A[65,75] = 1 # label: 3; middle grain; lightgray
A[75,30] = 1 # label: 4; bottom left; whitesmoke 
# A[85,70] = 1 # label: 5; bottom right; white

yBuffer = 5
yStart  = 30 + yBuffer

In [109]:
%matplotlib osx
fig, axs = plt.subplots(2,1,figsize=(6.4,8.4),gridspec_kw={'height_ratios': [3, 4]})
plt.suptitle("Migration of Blocking Energy of Growing Hematite Grains ")
with writer.saving(fig, "_11_CRM_DLA.mp4", dpi=200):
    for i in range(0,nParticles):
        x  = np.random.randint(0,maxX)
        y  = yStart
        
        while True:
            xOrg = x
            yOrg = y
            
            # plot step 
            r = np.random.random();
            if r <0.25 and r >= 0: # up   
                y=yOrg+1
            if r <0.50 and r>= 0.25: # down 
                y=yOrg-1
            if r <0.75 and r>= 0.50: # left
                x=xOrg-1
            if r <1.0 and r>= 0.75: # right
                x=xOrg+1
                
            # boundary conditions on x 
            if (x < 0):
                x = maxX - 1
            if(x == maxX):
                x = 0
            if (y < 0):
                y = maxY -1
            if(y == maxY):
                y = 0
            if (A[x,y] == 1): 
                x = xOrg
                y = yOrg
                continue   
            
            # Identifying neighbors
            xp = x + 1
            xm = x - 1
            yp = y + 1
            ym = y - 1
            if (xp == maxX):
                xp = 0
            if (xm < 0):
                xm = maxX - 1
            if (yp == maxY):
                yp = 0
            if (ym < 0):
                ym = maxY -1 
            
            # counting neighbors 
            n = 0
            if A[xp,y] == 1:
                n += 1
            if A[xm,y] == 1:
                n += 1
            if A[x,yp] == 1:
                n += 1
            if A[x,ym] == 1:
                n += 1
            
            # sticking probabilities 
            r2 = np.random.random()  
            p = 0.01
            if n == 0:
                p = 0
            if n == 1:
                p = p
            if n == 2:
                p = 70*p
            if n == 3:
                p = 100*p
            if n == 4:
                p = 100*p

            if r2 < p:
                A[x,y] = 1
                if (y+yBuffer>yStart and y+yBuffer<maxY): 
                    yStart = y+yBuffer
                if (i%100==0): 
                    print('i= {i} \tx={x} \ty={y} \tyStart={yStart}',i)
                nNewParticlesPerFrame = 50 #frame speed
                
            # plotting new particles 
                if (i%nNewParticlesPerFrame==0): 
                    display(A) 
                    display_volumes(A)
                    axs[0].legend(loc='upper right')    
                    plt.pause(0.01)
                    writer.grab_frame()
                        
                    
                break 
            if (yStart+1==maxY): 
                break
        
      

i= {i} 	x={x} 	y={y} 	yStart={yStart} 0
i= {i} 	x={x} 	y={y} 	yStart={yStart} 100
i= {i} 	x={x} 	y={y} 	yStart={yStart} 200
i= {i} 	x={x} 	y={y} 	yStart={yStart} 300
i= {i} 	x={x} 	y={y} 	yStart={yStart} 400
i= {i} 	x={x} 	y={y} 	yStart={yStart} 500
i= {i} 	x={x} 	y={y} 	yStart={yStart} 600
i= {i} 	x={x} 	y={y} 	yStart={yStart} 700
i= {i} 	x={x} 	y={y} 	yStart={yStart} 800
i= {i} 	x={x} 	y={y} 	yStart={yStart} 900
i= {i} 	x={x} 	y={y} 	yStart={yStart} 1000
i= {i} 	x={x} 	y={y} 	yStart={yStart} 1100
i= {i} 	x={x} 	y={y} 	yStart={yStart} 1200
i= {i} 	x={x} 	y={y} 	yStart={yStart} 1300
i= {i} 	x={x} 	y={y} 	yStart={yStart} 1400
i= {i} 	x={x} 	y={y} 	yStart={yStart} 1500
i= {i} 	x={x} 	y={y} 	yStart={yStart} 1600
i= {i} 	x={x} 	y={y} 	yStart={yStart} 1700
